In [1]:
import math
import random
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torch.distributions
from collections import namedtuple
from itertools import count

device = "cuda:0"

batchsize = 512
nsamples = 8
npoints = 5
emsize = 512


class Graph_Transformer(nn.Module):
    def __init__(self, emsize = 64, nhead = 8, nhid = 1024, nlayers = 4, ndecoderlayers = 2, dropout = 0):
        super().__init__()
        self.emsize = emsize
        from torch.nn import TransformerEncoder, TransformerEncoderLayer, TransformerDecoder, TransformerDecoderLayer
        encoder_layers = TransformerEncoderLayer(emsize, nhead, nhid, dropout = dropout)
        decoder_layers = TransformerDecoderLayer(emsize, nhead, nhid, dropout = dropout)
        self.transformer_encoder = TransformerEncoder(encoder_layers, nlayers)
        self.transformer_decoder = TransformerDecoder(decoder_layers, ndecoderlayers)
        self.encoder = nn.Linear(2, emsize)
        self.outputattention_query = nn.Linear(emsize, emsize, bias = False)
        self.outputattention_key = nn.Linear(emsize, emsize, bias = False)
        self.start_token = nn.Parameter(torch.randn([emsize], device = device))
        
        self.lineartest0 = nn.Linear(2, emsize)
        self.lineartest1 = nn.Linear(2, emsize)
        self.lineartest2 = nn.Linear(2, emsize)
        self.lineartest3 = nn.Linear(2 * emsize, emsize)
    
    def generate_subsequent_mask(self, sz): #last dimension will be softmaxed over when adding to attention logits, if boolean the ones turn into -inf
        #mask = (torch.triu(torch.ones(sz, sz)) == 1).transpose(0, 1)
        #mask = mask.float().masked_fill(mask == 0, float('-inf')).masked_fill(mask == 1, float(0.0))
        
        mask = torch.triu(torch.ones([sz, sz], dtype = torch.bool, device = device), diagonal = 1)
        return mask
    
    def encode(self, src): #src must be [batchsize * nsamples, npoints, 2]
        src = self.encoder(src).transpose(0, 1)
        output = self.transformer_encoder(src)
        return output #[npoints, batchsize * nsamples, emsize]
    
    def test_encode(self, src): #src must be [batchsize * nsamples, npoints = 5, 2]
        point_1 = self.lineartest1(src[:, 3, :] - 0.5) #want mean 0!!!!
        point_2 = self.lineartest1(src[:, 4, :] - 0.5)
        remaining = self.lineartest0(src[:, :3, :]) #[batchsize * nsamples, 3, emsize]
        point_1_message = self.lineartest1(src[:, 3, :] - 0.5).squeeze(1)
        point_2_message = self.lineartest2(src[:, 4, :] - 0.5).squeeze(1)
        point_1 = F.relu(torch.cat([point_1, point_2_message], dim = 1))
        point_2 = F.relu(torch.cat([point_2, point_1_message], dim = 1))
        point_1 = self.lineartest3(point_1)
        point_2 = self.lineartest3(point_2)
        src = torch.cat([torch.zeros_like(remaining.transpose(0, 1)), point_1.unsqueeze(0), point_2.unsqueeze(0)])
        return src #[npoints = 5, batchsize * nsamples, emsize]
    
    def decode_next(self, memory, tgt, route_mask): #route mask is [batchsize * nsamples, npoints], both memory and tgt must have batchsize and nsamples in same dimension (the 1th one)
        npoints = memory.size(0)
        batchsize = tgt.size(1)
        """if I really wanted this to be efficient I'd only recompute the decoder for the last tgt, and just remebering what the others looked like from before (won't change due to mask)"""
        """have the option to freeze the autograd on all but the last part of tgt, although at the moment this is a very natural way to say: initial choices matter more"""
        tgt_mask = self.generate_subsequent_mask(tgt.size(0))
        output = self.transformer_decoder(tgt, memory, tgt_mask) #[tgt, batchsize * nsamples, emsize]
        output_query = self.outputattention_query(memory).transpose(0, 1) #[batchsize * nsamples, npoints, emsize]
        output_key = self.outputattention_key(output[-1]) #[batchsize * nsamples, emsize]
        output_attention = torch.matmul(output_query * self.emsize ** -0.5, output_key.unsqueeze(-1)).squeeze(-1) #[batchsize * nsamples, npoints], technically don't need to scale attention as we divide by variance next anyway
        output_attention_tanh = output_attention.tanh() #[batchsize * nsamples, npoints]
        
        #we clone the route_mask incase we want to backprop using it (else it was modified by inplace opporations)
        output_attention = output_attention.masked_fill(route_mask.clone(), float('-inf')) #[batchsize * nsamples, npoints]
        output_attention_tanh = output_attention_tanh.masked_fill(route_mask.clone(), float('-inf')) #[batchsize * nsamples, npoints]
        
        return output_attention_tanh, output_attention #[batchsize * nsamples, npoints]
    
    def calculate_logprob(self, memory, routes): #memory is [npoints, batchsize * nsamples, emsize], routes is [batchsize * nsamples, npoints - 3], rather than backproping the entire loop, this saves vram (and computation)
        npoints = memory.size(0)
        ninternalpoints = routes.size(1)
        bigbatchsize = memory.size(1)
        memory_ = memory.gather(0, routes.transpose(0, 1).unsqueeze(2).expand(-1, -1, self.emsize)) #[npoints - 3, batchsize * nsamples, emsize] reorder memory into order of routes
        tgt = torch.cat([self.start_token.unsqueeze(0).unsqueeze(1).expand(1, bigbatchsize, -1), memory_[:-1]]) #[npoints - 3, batchsize * nroutes, emsize], want to go from memory to tgt
        tgt_mask = self.generate_subsequent_mask(ninternalpoints)
        output = self.transformer_decoder(tgt, memory, tgt_mask) #[npoints - 3, batchsize * nsamples, emsize]
        """want probability of going from key to query, but first need to normalise (softmax with mask)"""
        output_query = self.outputattention_query(memory_).transpose(0, 1) #[batchsize * nsamples, npoints - 3, emsize]
        output_key = self.outputattention_key(output).transpose(0, 1) #[batchsize * nsamples, npoints - 3, emsize]
        attention_mask = torch.full([ninternalpoints, ninternalpoints], True, dtype = torch.bool, device = device).triu(1) #[npoints - 3, npoints - 3], True for i < j
        output_attention = torch.matmul(output_query * self.emsize ** -0.5, output_key.transpose(-1, -2))
        """quick fix to stop divergence"""
        output_attention_tanh = output_attention.tanh()
        
        output_attention_tanh = output_attention_tanh.masked_fill(attention_mask, float('-inf'))
        output_attention_tanh = output_attention_tanh - output_attention_tanh.logsumexp(-2, keepdim = True) #[batchsize * nsamples, npoints - 3, npoints - 3]
        
        output_attention = output_attention.masked_fill(attention_mask, float('-inf'))
        output_attention = output_attention - output_attention.logsumexp(-2, keepdim = True) #[batchsize * nsamples, npoints - 3, npoints - 3]
        
        """infact I'm almost tempted to not mask choosing a previous point, so it's forced to learn it and somehow incorporate it into its computation, but without much impact on reinforcing good examples"""
        logprob_tanh = output_attention_tanh.diagonal(dim1 = -1, dim2 = -2).sum(-1) #[batchsize * nsamples]
        logprob = output_attention.diagonal(dim1 = -1, dim2 = -2).sum(-1) #[batchsize * nsamples]
        return logprob_tanh, logprob #[batchsize * nsamples]

NN = Graph_Transformer().to(device)
optimizer = optim.Adam(NN.parameters())


class environment():
    def reset(self, npoints, batchsize, nsamples):
        if npoints <= 3:
            print("Error: not enough points for valid problem instance")
            return
        self.batchsize = batchsize * nsamples #so that I don't have to rewrite all this code, we store these two dimensions together
        self.nsamples = nsamples
        self.npoints = npoints
        self.points = torch.rand([batchsize, npoints - 3, 2], device = device).unsqueeze(1).expand(-1, nsamples, -1, -1).reshape(self.batchsize, npoints - 3, 2)
        self.corner_points = torch.tensor([[0, 0], [2, 0], [0, 2]], dtype = torch.float, device = device)
        self.points = torch.cat([self.corner_points.unsqueeze(0).expand(self.batchsize, -1, -1), self.points], dim = -2) #[batchsize * nsamples, npoints, 2]
        self.points_mask = torch.cat([torch.ones([self.batchsize, 3], dtype = torch.bool, device = device), torch.zeros([self.batchsize, npoints - 3], dtype = torch.bool, device = device)], dim = 1)
        self.points_sequence = torch.empty([self.batchsize, 0], dtype = torch.long, device = device)
        
        """use a trick, for the purpose of an 'external' triangle that is always left untouched, which means we don't have to deal with boundary edges as being different. external triangle is [0, 1, 2] traversed clockwise..."""
        self.partial_delaunay_triangles = torch.tensor([[0, 2, 1], [0, 1, 2]], dtype = torch.int64, device = device).unsqueeze(0).expand(self.batchsize, -1, -1).contiguous() #[batchsize, ntriangles, 3] contains index of points, always anticlockwise
        self.partial_delaunay_edges = torch.tensor([5, 4, 3, 2, 1, 0], dtype = torch.int64, device = device).unsqueeze(0).expand(self.batchsize, -1).contiguous() #[batchsize, ntriangles * 3] contains location of corresponding edge (edges go in order 01, 12, 20). Edges will always flip since triangles are stored anticlockwise.
        
        self.ntriangles = 2 #can store as scalar, since will always be the same
        self.cost = torch.zeros([self.batchsize], device = device)
        
        self.logprob = torch.zeros([self.batchsize], device = device, requires_grad = True)
    
    def update(self, point_index): #point_index is [batchsize]
        if point_index.size(0) != self.batchsize:
            print("Error: point_index.size() doesn't match expected size, should be [batchsize]")
            return
        if self.points_mask.gather(1, point_index.unsqueeze(1)).sum():
            print("Error: some points already added")
            return
        triangles_coordinates = self.points.gather(1, self.partial_delaunay_triangles.view(self.batchsize, self.ntriangles * 3).unsqueeze(2).expand(-1, -1, 2)).view(self.batchsize, self.ntriangles, 3, 2) #[batchsize, ntriangles, 3, 2]
        newpoint = self.points.gather(1, point_index.unsqueeze(1).unsqueeze(2).expand(self.batchsize, 1, 2)).squeeze(1) #[batchsize, 2]
        
        incircle_matrix = torch.cat([triangles_coordinates, newpoint.unsqueeze(1).unsqueeze(2).expand(-1, self.ntriangles, 1, -1)], dim = -2) #[batchsize, ntriangles, 4, 2]
        incircle_matrix = torch.cat([incircle_matrix, (incircle_matrix * incircle_matrix).sum(-1, keepdim = True), torch.ones([self.batchsize, self.ntriangles, 4, 1], device = device)], dim = -1) #[batchsize, ntriangles, 4, 4]
        incircle_test = incircle_matrix.det() > 0 #[batchsize, ntriangles], is True if inside incircle
        removed_edge_mask = incircle_test.unsqueeze(2).expand(-1, -1, 3).reshape(-1) #[batchsize * ntriangles * 3]
        
        edges = (self.partial_delaunay_edges + self.ntriangles * 3 * torch.arange(self.batchsize, device = device).unsqueeze(1)).view(-1) #[batchsize * ntriangles * 3]
        neighbouring_edge = edges.masked_select(removed_edge_mask)
        neighbouring_edge_mask = torch.zeros([self.batchsize * self.ntriangles * 3], device = device, dtype = torch.bool)
        neighbouring_edge_mask[neighbouring_edge] = True
        neighbouring_edge_mask = (neighbouring_edge_mask * removed_edge_mask.logical_not()) #[batchsize * ntriangles * 3]
        
        n_new_triangles = neighbouring_edge_mask.view(self.batchsize, -1).sum(-1) #[batchsize]
        
        new_point = point_index.unsqueeze(1).expand(-1, self.ntriangles * 3).masked_select(neighbouring_edge_mask.view(self.batchsize, -1))
        
        second_point_mask = neighbouring_edge_mask.view(self.batchsize, -1, 3) #[batchsize, ntriangles 3]
        (first_point_indices0, first_point_indices1, first_point_indices2) = second_point_mask.nonzero(as_tuple = True)
        first_point_indices2 = (first_point_indices2 != 2) * (first_point_indices2 + 1)
        
        first_point = self.partial_delaunay_triangles[first_point_indices0, first_point_indices1, first_point_indices2] #[?]
        second_point = self.partial_delaunay_triangles.masked_select(second_point_mask) #[?]
        
        new_triangles_mask = torch.cat([incircle_test, torch.ones([self.batchsize, 2], dtype = torch.bool, device = device)], dim = 1) #[batchsize, ntriangles + 2]
        
        new_neighbouring_edges = 3 * new_triangles_mask.nonzero(as_tuple = True)[1] #[?], 3* since is the 01 edge of new triangles (see later)
        self.partial_delaunay_edges.masked_scatter_(neighbouring_edge_mask.view(self.batchsize, -1), new_neighbouring_edges) #still [batchsize, ntriangles * 3] for now
        
        self.partial_delaunay_triangles = torch.cat([self.partial_delaunay_triangles, torch.empty([self.batchsize, 2, 3], dtype = torch.long, device = device)], dim = 1)
        self.partial_delaunay_edges = torch.cat([self.partial_delaunay_edges, torch.empty([self.batchsize, 6], dtype = torch.long, device = device)], dim = 1)
        new_triangles = torch.stack([first_point, second_point, new_point], dim = 1) #[?, 3], edge here is flipped compared to edge in neighbouring triangle (so first_point is the second point in neighbouring edge)
        self.partial_delaunay_triangles.masked_scatter_(new_triangles_mask.unsqueeze(2).expand(-1, -1, 3), new_triangles) #[batchsize, ntriangles + 2, 3]
        
        new_edge01 = neighbouring_edge_mask.view(self.batchsize, -1).nonzero(as_tuple = True)[1] #[?]
        
        """we are currently storing which triangles have to be inserted, via the edges along the perimeter of the delaunay cavity, we need to compute which edge is to the 'left'/'right' of each edge"""
        """don't have the memory to do a batchsize * n * n boolean search, don't have the speed to do a batchsize^2 search (as would be the case for sparse matrix or similar)"""
        """best alternative: rotate the edge around right point, repeat until hit edge in mask (will never go to an edge of a removed triangle before we hit edge in mask) should basically be order 1!!!!!"""
        
        neighbouring_edge_index = neighbouring_edge_mask.nonzero(as_tuple = True)[0] #[?]
        next_neighbouring_edge_index = torch.empty_like(neighbouring_edge_index) #[?]
        
        rotating_flipped_neighbouring_edge_index = neighbouring_edge_mask.nonzero(as_tuple = True)[0] #[?], initialise
        todo_mask = torch.ones_like(next_neighbouring_edge_index, dtype = torch.bool) #[?]
        while todo_mask.sum():
            rotating_neighbouring_edge_index = rotating_flipped_neighbouring_edge_index + 1 - 3 * (rotating_flipped_neighbouring_edge_index % 3 == 2) #[todo_mask.sum()], gets smaller until nothing left EFFICIENCY (this may be seriously stupid, as it requires making a bunch of copies when I could be doing stuff inplace)
            
            update_mask = neighbouring_edge_mask[rotating_neighbouring_edge_index] #[todo_mask.sum()]
            update_mask_unravel = torch.zeros_like(todo_mask).masked_scatter(todo_mask, update_mask) #[?]
            
            next_neighbouring_edge_index.masked_scatter_(update_mask_unravel, rotating_neighbouring_edge_index.masked_select(update_mask)) #[?]
            
            todo_mask.masked_fill_(update_mask_unravel, False) #[?]
            rotating_flipped_neighbouring_edge_index = edges[rotating_neighbouring_edge_index.masked_select(update_mask.logical_not())] #[todo_mask.sum()]
        triangle_index = new_triangles_mask.view(-1).nonzero(as_tuple = True)[0] #[?], index goes up to batchsize * (ntriangles + 2), this is needed for when we invert the permutation by scattering (won't scatter same number of triangles per batch)
        
        next_triangle_index = torch.empty_like(edges).masked_scatter_(neighbouring_edge_mask, triangle_index)[next_neighbouring_edge_index] #[?], index goes up to batchsize * (ntriangles + 2)
        next_edge = 3 * next_triangle_index + 1 #[?]
        
        invert_permutation = torch.empty_like(new_triangles_mask.view(-1), dtype=torch.long) #[batchsize * (ntriangles + 2)]
        invert_permutation[next_triangle_index] = triangle_index #[batchsize * (ntriangles + 2)]
        previous_triangle_index = invert_permutation.masked_select(new_triangles_mask.view(-1)) #[?]
        previous_edge = 3 * previous_triangle_index + 2 #[?]
        
        """in the above we rotated around 'first_point' in our new triangles"""
        new_edge20 = next_edge % ((self.ntriangles + 2) * 3) #[?]
        new_edge12 = previous_edge % ((self.ntriangles + 2) * 3) #[?]
        
        new_edges = torch.stack([new_edge01, new_edge12, new_edge20], dim = 1) #[?, 3]
        self.partial_delaunay_edges.masked_scatter_(new_triangles_mask.unsqueeze(2).expand(-1, -1, 3).reshape(self.batchsize, -1), new_edges) #[batchsize, (ntriangles + 2) * 3]
        
        self.ntriangles += 2
        """currently only count the extra triangles you replace (not the on you have to remove because you're located there, and not the ones you make because you have to create two more"""
        self.cost += (n_new_triangles - 3)
        self.points_mask.scatter_(1, point_index.unsqueeze(1).expand(-1, self.npoints), True)
        self.points_sequence = torch.cat([self.points_sequence, point_index.unsqueeze(1)], dim = 1)
    
    def sample_point(self, logits): #logits must be [batchsize * nsamples, npoints]
        probs = torch.distributions.categorical.Categorical(logits = logits)
        next_point = probs.sample() #size is [batchsize * nsamples]
        self.update(next_point)
        self.logprob = self.logprob + probs.log_prob(next_point)
        return next_point #[batchsize * nsamples]
    
    def sampleandgreedy_point(self, logits): #logits must be [batchsize * nsamples, npoints], last sample will be the greedy choice (but we still need to keep track of its logits)
        logits_sample = logits.view(-1, self.nsamples, self.npoints)[:, :-1, :]
        probs = torch.distributions.categorical.Categorical(logits = logits_sample)
        
        sample_point = probs.sample() #[batchsize, (nsamples - 1)]
        greedy_point = logits.view(-1, self.nsamples, self.npoints)[:, -1, :].max(-1, keepdim = True)[1] #[batchsize, 1]
        next_point = torch.cat([sample_point, greedy_point], dim = 1).view(-1)
        self.update(next_point)
        self.logprob = self.logprob + torch.cat([probs.log_prob(sample_point), torch.zeros([sample_point.size(0), 1], device = device)], dim = 1).view(-1)
        return next_point
    

env = environment()


def train(epochs = 300000, npoints = 13, batchsize = 2000, nsamples = 8):
    NN.train()
    for i in range(epochs):
        env.reset(npoints, batchsize, nsamples)
        """include the boundary points, kinda makes sense that they should contribute (atm only in the encoder, difficult to see how in the decoder)"""
        memory = NN.encode(env.points) #[npoints, batchsize * nsamples, emsize]
        #### #### #### remember to include tgt.detach() when reinstate with torch.no_grad()
        tgt = NN.start_token.unsqueeze(0).unsqueeze(1).expand(1, batchsize * nsamples, -1).detach() #[1, batchsize * nsamples, emsize]
        #with torch.no_grad(): #to speed up computation, selecting routes is done without gradient
        with torch.no_grad():
            for j in range(3, npoints):
                #### #### #### remember to include memory.detach() when reinstate with torch.no_grad()
                _, logits = NN.decode_next(memory.detach(), tgt, env.points_mask)
                next_point = env.sampleandgreedy_point(logits)
                """
                for inputing the previous embedding into decoder
                """
                tgt = torch.cat([tgt, memory.gather(0, next_point.unsqueeze(0).unsqueeze(2).expand(1, -1, memory.size(2)))]) #[nsofar, batchsize * nsamples, emsize]
                """
                for inputing the previous decoder output into the decoder (allows for an evolving strategy, but doesn't allow for fast training
                """
                ############

        
        NN.eval()
        _, logprob = NN.calculate_logprob(memory, env.points_sequence) #[batchsize * nsamples]
        NN.train()
        """
        clip logprob so doesn't reinforce things it already knows
        TBH WANT SOMETHING DIFFERENT ... want to massively increase training if find something unexpected and otherwise not
        """
        greedy_prob = logprob.view(batchsize, nsamples)[:, -1].detach() #[batchsize]
        greedy_baseline = env.cost.view(batchsize, nsamples)[:, -1] #[batchsize], greedy sample
        fixed_baseline = 0.5 * torch.ones([1], device = device)
        min_baseline = env.cost.view(batchsize, nsamples)[:, :-1].min(-1)[0] #[batchsize], minimum cost
        baseline = greedy_baseline
        regular_reinforcement = env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1)
        positive_reinforcement = - F.relu( - (env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1))) <= -0.05 #don't scale positive reinforcement
        negative_reinforcement = F.relu(env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1)) > 1
        positive_reinforcement_binary = env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1) <= -0.05
        negative_reinforcement_binary = env.cost.view(batchsize, nsamples)[:, :-1] - baseline.unsqueeze(1) > 1
        """
        binary positive reinforcement
        """
        #loss = - ((logprob.view(batchsize, nsamples)[:, :-1] < -0.2) * logprob.view(batchsize, nsamples)[:, :-1] * positive_reinforcement_binary).mean() #+ (logprob.view(batchsize, nsamples)[:, :-1] > -1) * logprob.view(batchsize, nsamples)[:, :-1] * negative_reinforcement_binary
        """
        clipped binary reinforcement
        """
        #loss = ( 
        #        - logprob.view(batchsize, nsamples)[:, :-1] 
        #        #* (logprob.view(batchsize, nsamples)[:, :-1] < 0) 
        #        * positive_reinforcement_binary 
        #        + logprob.view(batchsize, nsamples)[:, :-1] 
        #        #* (logprob.view(batchsize, nsamples)[:, :-1] > greedy_prob.unsqueeze(1) - 6) 
        #        * negative_reinforcement_binary 
        #).mean()
        """
        clipped binary postive, clipped weighted negative
        """
        #loss = ( - logprob.view(batchsize, nsamples)[:, :-1] * (logprob.view(batchsize, nsamples)[:, :-1] < -0.2) * positive_reinforcement_binary + logprob.view(batchsize, nsamples)[:, :-1] * (logprob.view(batchsize, nsamples)[:, :-1] > -2) * negative_reinforcement ).mean()
        """
        clipped reinforcement without rescaling
        """
        #loss = ((logprob.view(batchsize, nsamples)[:, :-1] < -0.7) * logprob.view(batchsize, nsamples)[:, :-1] * positive_reinforcement + (logprob.view(batchsize, nsamples)[:, :-1] > -5) * logprob.view(batchsize, nsamples)[:, :-1] * negative_reinforcement).mean()
        """
        clipped reinforcement
        """
        #loss = (logprob.view(batchsize, nsamples)[:, :-1] * positive_reinforcement / (positive_reinforcement.var() + 0.001).sqrt() + (logprob.view(batchsize, nsamples)[:, :-1] > -3) * logprob.view(batchsize, nsamples)[:, :-1] * negative_reinforcement / (negative_reinforcement.var() + 0.001).sqrt()).mean()
        """
        balanced reinforcement
        """
        #loss = (logprob.view(batchsize, nsamples)[:, :-1] * (positive_reinforcement / (positive_reinforcement.var() + 0.001).sqrt() + negative_reinforcement / (negative_reinforcement.var() + 0.001).sqrt())).mean()
        """
        regular loss with thresholding
        """
        loss = (logprob.view(batchsize, nsamples)[:, :-1] * regular_reinforcement * (positive_reinforcement_binary + negative_reinforcement_binary)).mean()
        """
        regular loss
        """
        #loss = (logprob.view(batchsize, nsamples)[:, :-1] * (positive_reinforcement + negative_reinforcement)).mean()
        optimizer.zero_grad()
        loss.backward()
        #print(NN.encoder.weight.grad)
        optimizer.step()
        #print(greedy_baseline.mean().item())
        print(greedy_baseline.mean().item(), logprob.view(batchsize, nsamples)[:, -1].mean().item(), logprob.view(batchsize, nsamples)[:, :-1].mean().item(), logprob[batchsize - 1].item(), logprob[0].item(), env.logprob[0].item())
  

In [2]:
train(300000, 23, 700, 8)

36.47142791748047 -41.39678192138672 -42.31098175048828 -42.27156448364258 -42.346458435058594 -42.34646224975586
34.31999969482422 -40.667015075683594 -42.255428314208984 -42.71338653564453 -42.10069274902344 -42.10069274902344
35.591426849365234 -34.30012893676758 -40.032508850097656 -39.828941345214844 -37.18412780761719 -37.18413162231445
32.18571472167969 -30.173479080200195 -37.179752349853516 -35.95885467529297 -39.539344787597656 -39.53934097290039
33.23143005371094 -23.10694694519043 -30.669801712036133 -30.315139770507812 -36.0340576171875 -36.0340576171875
33.082855224609375 -23.8819522857666 -30.002710342407227 -27.208974838256836 -31.952980041503906 -31.95298194885254
32.567142486572266 -21.972707748413086 -28.105268478393555 -30.192054748535156 -27.934734344482422 -27.93473243713379
32.492855072021484 -19.706205368041992 -26.66964340209961 -26.02834129333496 -26.324771881103516 -26.32476806640625
31.69999885559082 -17.31521224975586 -24.21059226989746 -20.108367919921875 

31.247142791748047 -2.1358678340911865 -4.040246963500977 -7.8234758377075195 -1.991621971130371 -1.9916136264801025
31.411428451538086 -2.198409080505371 -4.169000625610352 -9.66489315032959 -1.4597697257995605 -1.4597697257995605
31.3028564453125 -2.094587802886963 -4.0005412101745605 -6.5757060050964355 -4.073453903198242 -4.073461532592773
31.398571014404297 -2.1634414196014404 -4.079352855682373 -4.9302263259887695 -2.490797996520996 -2.490799903869629
31.19285774230957 -2.2063801288604736 -4.239185333251953 -2.3751370906829834 -8.639394760131836 -8.639398574829102
31.265714645385742 -2.3061981201171875 -4.4048357009887695 -1.313281774520874 -7.028393745422363 -7.028404235839844
31.347143173217773 -2.4242115020751953 -4.524718761444092 -1.8604936599731445 -2.131488561630249 -2.1314923763275146
31.608572006225586 -2.4809224605560303 -4.657044410705566 -3.145212173461914 -2.714996337890625 -2.7149829864501953
31.50857162475586 -2.416797637939453 -4.635242462158203 -3.419968605041504

31.28999900817871 -1.4730054140090942 -2.858003854751587 -3.0752809047698975 -1.8830623626708984 -1.8830549716949463
31.112855911254883 -1.5118324756622314 -2.827860116958618 -3.856684923171997 -0.9545708894729614 -0.9545718431472778
31.40999984741211 -1.4910999536514282 -2.823963165283203 -3.5897607803344727 -5.601061820983887 -5.601046562194824
31.314285278320312 -1.5440617799758911 -2.8715577125549316 -2.9554309844970703 -5.66914701461792 -5.66914701461792
31.435714721679688 -1.4225913286209106 -2.6829469203948975 -1.6111822128295898 -4.26420259475708 -4.264228820800781
31.295713424682617 -1.4017354249954224 -2.702502727508545 -0.8910245895385742 -1.8373394012451172 -1.8373489379882812
31.402856826782227 -1.445671558380127 -2.8415026664733887 -2.0981979370117188 -2.101231575012207 -2.1012353897094727
31.342857360839844 -1.5593680143356323 -3.0199971199035645 -2.057861328125 -5.415102958679199 -5.415096282958984
31.510000228881836 -1.6478593349456787 -3.2107462882995605 -1.8206840753

31.488571166992188 -1.6780928373336792 -3.2258729934692383 -3.3684422969818115 -2.052837610244751 -2.052837371826172
31.432857513427734 -1.6285560131072998 -3.138930559158325 -5.868391513824463 -2.196133613586426 -2.1961491107940674
31.35714340209961 -1.5461113452911377 -2.9729506969451904 -4.43049430847168 -5.35237455368042 -5.3523759841918945
31.412857055664062 -1.4504989385604858 -2.8002829551696777 -0.2648024559020996 -0.8224954605102539 -0.8224916458129883
31.47142791748047 -1.3635812997817993 -2.590360403060913 -1.0159695148468018 -0.7466115951538086 -0.7466135025024414
31.18000030517578 -1.3530555963516235 -2.5695507526397705 -5.511058330535889 -2.8468918800354004 -2.846895694732666
31.20857048034668 -1.3776564598083496 -2.6127753257751465 -6.579303741455078 -1.607692003250122 -1.6076842546463013
31.417142868041992 -1.4873499870300293 -2.814743757247925 -5.549163818359375 -2.3152832984924316 -2.3152823448181152
31.282855987548828 -1.5310198068618774 -2.9244275093078613 -4.119047

31.378570556640625 -1.6432393789291382 -3.0883145332336426 -4.273229598999023 -4.756776809692383 -4.756776809692383
31.064285278320312 -1.6680716276168823 -3.1803383827209473 -2.1622238159179688 -7.944446563720703 -7.944446563720703
31.238571166992188 -1.6285110712051392 -3.046543598175049 -4.379417419433594 -4.060998916625977 -4.061014175415039
31.354286193847656 -1.5550507307052612 -2.969527244567871 -2.731952667236328 -4.705881118774414 -4.70588493347168
31.149999618530273 -1.3624358177185059 -2.626121759414673 -2.8024215698242188 -2.50998592376709 -2.509974479675293
30.959999084472656 -1.2647355794906616 -2.446674108505249 -2.972005844116211 -3.3098697662353516 -3.309856414794922
31.038570404052734 -1.18306565284729 -2.2932584285736084 -0.40788745880126953 -0.41425132751464844 -0.41425132751464844
31.342857360839844 -1.1453957557678223 -2.245136022567749 -0.47431373596191406 -0.14208447933197021 -0.14208447933197021
31.53999900817871 -1.1669729948043823 -2.286712646484375 -0.939663

...

34.86428451538086 -34.598392486572266 -40.44096755981445 -37.625 -40.875 -40.375
34.755714416503906 -35.37553405761719 -40.32341766357422 -45.5 -36.125 -36.875
34.74571228027344 -37.70803451538086 -40.30535888671875 -42.125 -39.25 -38.75
34.89285659790039 -38.30356979370117 -40.52923583984375 -40.0 -38.125 -36.375
34.61000061035156 -36.570892333984375 -40.66803741455078 -38.75 -39.5 -39.5
34.81142807006836 -35.99856948852539 -40.6360969543457 -42.875 -39.75 -40.5
34.849998474121094 -34.817142486572266 -41.00397872924805 -43.75 -41.0 -40.0
34.994285583496094 -36.87821578979492 -40.051937103271484 -39.0 -41.25 -41.375
34.76142883300781 -36.25642776489258 -40.49140167236328 -44.125 -37.875 -38.375
34.70000076293945 -36.51374816894531 -40.05660629272461 -40.25 -42.0 -42.625
34.79999923706055 -37.074283599853516 -41.04645538330078 -38.5 -38.75 -38.375
34.65571212768555 -37.707855224609375 -40.71147918701172 -42.25 -42.75 -43.75
34.92571258544922 -37.85499954223633 -41.00408172607422 -43.625

34.77571487426758 -33.481605529785156 -36.4480094909668 -33.375 -34.125 -34.375
34.66714096069336 -34.36714172363281 -36.727272033691406 -37.625 -34.0 -32.5
34.84714126586914 -33.250892639160156 -36.51466751098633 -32.0 -34.75 -34.375
34.70000076293945 -32.82892990112305 -36.481529235839844 -34.5 -34.5 -35.0
34.772857666015625 -33.714820861816406 -36.73405456542969 -33.375 -35.875 -35.625
34.86000061035156 -33.74142837524414 -36.855995178222656 -42.875 -41.875 -42.375
34.88428497314453 -33.66553497314453 -36.56525421142578 -39.25 -33.25 -32.5
34.849998474121094 -33.48589324951172 -36.7803840637207 -34.25 -35.375 -35.0
34.808570861816406 -33.64589309692383 -37.18803405761719 -33.75 -38.625 -39.0
34.56999969482422 -34.58106994628906 -37.1363525390625 -35.75 -36.125 -35.125
34.71285629272461 -34.01678466796875 -37.347347259521484 -44.875 -38.875 -39.25
34.7071418762207 -33.81535720825195 -37.443878173828125 -36.0 -39.0 -39.0
34.58714294433594 -33.37535858154297 -37.45290756225586 -34.25 -

34.67142868041992 -32.64500045776367 -33.667396545410156 -32.75 -31.625 -31.5
34.652854919433594 -32.82178497314453 -33.783164978027344 -30.625 -33.875 -33.75
34.727142333984375 -32.81106948852539 -33.742881774902344 -35.375 -31.625 -31.75
34.939998626708984 -32.585357666015625 -33.58959197998047 -30.75 -34.375 -33.625
34.61428451538086 -32.66035842895508 -33.747703552246094 -32.875 -35.0 -35.5
34.56285858154297 -32.599998474121094 -33.62040710449219 -34.125 -33.5 -33.625
34.7928581237793 -32.766963958740234 -33.70086669921875 -35.75 -32.375 -32.125
34.672855377197266 -32.605892181396484 -33.7202033996582 -42.0 -33.125 -33.125
35.03571319580078 -32.459999084472656 -33.54043197631836 -33.875 -32.125 -32.125
34.755714416503906 -32.613929748535156 -33.60362243652344 -38.75 -30.875 -30.625
34.74142837524414 -32.49196243286133 -33.43089294433594 -34.25 -31.625 -31.375
34.7071418762207 -32.416072845458984 -33.376426696777344 -30.125 -31.625 -31.5
34.702857971191406 -32.340179443359375 -33.23

34.65571212768555 -30.84160614013672 -31.084514617919922 -30.25 -30.5 -30.25
34.90571212768555 -30.834285736083984 -31.04645347595215 -30.25 -32.625 -32.0
34.64285659790039 -30.808393478393555 -31.021886825561523 -30.5 -30.5 -30.125
34.605712890625 -30.896785736083984 -31.109437942504883 -31.5 -30.875 -31.25
34.584285736083984 -30.95857048034668 -31.12757682800293 -31.25 -31.25 -30.5
34.7542839050293 -30.880178451538086 -31.090484619140625 -30.875 -37.0 -37.125
34.452857971191406 -30.914106369018555 -31.12456703186035 -31.875 -30.125 -30.625
34.637142181396484 -30.92517852783203 -31.139999389648438 -32.0 -30.375 -30.5
34.68428421020508 -30.979286193847656 -31.189973831176758 -30.625 -31.125 -31.125
34.64142990112305 -30.93964195251465 -31.14392852783203 -30.625 -31.0 -31.0
34.591426849365234 -30.911964416503906 -31.1448974609375 -32.125 -30.875 -30.875
34.779998779296875 -30.972679138183594 -31.1674747467041 -31.375 -30.375 -30.125
34.79428482055664 -30.943927764892578 -31.174718856811

KeyboardInterrupt: 

In [ ]:
train(300000, 13, 2000, 8) #thresholding

11.54050064086914 -14.765214920043945 -15.096917152404785 -14.775527000427246 -15.066579818725586 -15.06657886505127
11.25100040435791 -13.407490730285645 -14.888965606689453 -12.757770538330078 -14.944479942321777 -14.944480895996094
11.091500282287598 -10.518348693847656 -13.41714859008789 -10.127902030944824 -14.893556594848633 -14.8935546875
11.219000816345215 -7.846808910369873 -11.030125617980957 -8.178133010864258 -11.225786209106445 -11.225785255432129
11.33750057220459 -8.734872817993164 -11.40661907196045 -8.069746017456055 -8.800930976867676 -8.800930976867676
11.174500465393066 -6.389033794403076 -9.358418464660645 -5.79541015625 -5.576928615570068 -5.57692813873291
11.288000106811523 -6.3528733253479 -9.035102844238281 -7.682464122772217 -6.3702073097229 -6.3702073097229
11.338000297546387 -7.346500396728516 -9.937580108642578 -5.836763381958008 -7.50450325012207 -7.504504203796387
11.326000213623047 -6.458800792694092 -9.104236602783203 -5.3357343673706055 -13.28193187713

10.782000541687012 -1.9513280391693115 -3.28420352935791 -2.039769172668457 -0.8216821551322937 -0.8216821551322937
10.93850040435791 -1.567481279373169 -2.7480850219726562 -0.6428316235542297 -4.51395320892334 -4.513952255249023
10.853500366210938 -1.6560245752334595 -2.883864164352417 -0.8281278610229492 -4.1347808837890625 -4.134779930114746
10.791500091552734 -2.0465781688690186 -3.5168206691741943 -0.8503934144973755 -2.866718292236328 -2.8667125701904297
10.718500137329102 -2.4226598739624023 -4.105042934417725 -3.1161906719207764 -3.5024869441986084 -3.5024874210357666
10.641500473022461 -2.745328426361084 -4.539624214172363 -2.1051313877105713 -1.5745048522949219 -1.574502944946289
10.73900032043457 -2.55440092086792 -4.318938255310059 -2.2692863941192627 -2.206836462020874 -2.206840991973877
10.645500183105469 -2.0969276428222656 -3.70805025100708 -4.194189071655273 -6.116789817810059 -6.116789817810059
10.63900089263916 -1.8789900541305542 -3.3734307289123535 -2.9751472473144

10.404500961303711 -1.0803089141845703 -2.067189931869507 -0.8012866973876953 -0.38088205456733704 -0.3808800280094147
10.346000671386719 -1.0822582244873047 -2.0801587104797363 -1.3645305633544922 -0.1862497329711914 -0.1862497329711914
10.380500793457031 -1.055126428604126 -2.0064263343811035 -4.25355339050293 -1.006737470626831 -1.0067412853240967
10.397500038146973 -1.084294080734253 -2.0774383544921875 -0.9314384460449219 -3.1927003860473633 -3.1926965713500977
10.582500457763672 -1.101689338684082 -2.1328306198120117 -1.0139503479003906 -3.7748947143554688 -3.7748985290527344
10.521500587463379 -1.1066919565200806 -2.1451685428619385 -0.606863260269165 -3.3759212493896484 -3.3759231567382812
10.467500686645508 -1.0256603956222534 -1.9781743288040161 -0.333984375 -2.31284236907959 -2.31284236907959
10.460500717163086 -1.0275508165359497 -1.959566354751587 -1.2070586681365967 -1.4001502990722656 -1.4001502990722656
10.480000495910645 -0.9941502809524536 -1.9090008735656738 -0.72064

10.353500366210938 -1.086888074874878 -2.07942795753479 -1.517512321472168 -0.9308109283447266 -0.930811882019043
10.262500762939453 -1.0816056728363037 -2.035895586013794 -0.6748676300048828 -1.2403430938720703 -1.2403430938720703
10.259000778198242 -1.072878360748291 -2.056781768798828 -1.2795934677124023 -2.6136436462402344 -2.6136474609375
10.229000091552734 -1.0648167133331299 -2.055948495864868 -0.7151050567626953 -2.1825790405273438 -2.182577133178711
10.228500366210938 -1.0863479375839233 -2.0755975246429443 -2.6713109016418457 -2.2827582359313965 -2.2827582359313965
10.225500106811523 -1.030704140663147 -2.0173823833465576 -0.5812807083129883 -1.1871542930603027 -1.1871533393859863
10.209500312805176 -1.0058913230895996 -1.943392276763916 -1.480614185333252 -1.7349563837051392 -1.7349563837051392
10.315500259399414 -1.0117384195327759 -1.9427493810653687 -0.9160451889038086 -1.1269453763961792 -1.1269491910934448
10.203500747680664 -1.059579610824585 -2.044858694076538 -0.9199

10.118500709533691 -0.8130624294281006 -1.5609867572784424 -0.42972660064697266 -4.179012775421143 -4.179012775421143
10.171500205993652 -0.873116135597229 -1.7061792612075806 -0.49871838092803955 -0.4518880844116211 -0.4518871307373047
10.187000274658203 -0.920896053314209 -1.7770839929580688 -1.1512908935546875 -0.036638736724853516 -0.036638736724853516
10.16550064086914 -0.9660690426826477 -1.8588013648986816 -1.9660320281982422 -0.09657931327819824 -0.09657931327819824
10.18850040435791 -0.9606606960296631 -1.844024896621704 -0.6685800552368164 -0.10035514831542969 -0.10035514831542969
10.233000755310059 -0.8986017107963562 -1.7412854433059692 -0.042272090911865234 -1.2962727546691895 -1.2962727546691895
10.194000244140625 -0.8646177649497986 -1.6876360177993774 -1.8211431503295898 -1.38525390625 -1.38525390625
10.061500549316406 -0.8493252396583557 -1.6582262516021729 -0.7383079528808594 -0.18835830688476562 -0.18835830688476562
9.996500015258789 -0.8255448341369629 -1.6148679256

...

7.44450044631958 -0.5954077243804932 -1.209234595298767 -0.0028514862060546875 -0.09088134765625 -0.09088134765625
7.410500526428223 -0.5986236333847046 -1.2049570083618164 -1.2105159759521484 -0.30014991760253906 -0.30014991760253906
7.469500541687012 -0.5895211100578308 -1.1892427206039429 -0.0293731689453125 -0.8375396728515625 -0.8375434875488281
7.447000503540039 -0.6115856170654297 -1.2140628099441528 -0.09577226638793945 -0.22636651992797852 -0.22636651992797852
7.4185004234313965 -0.6060101389884949 -1.216976284980774 -1.6367683410644531 -0.11513519287109375 -0.11513519287109375
7.444000244140625 -0.5946013331413269 -1.2060644626617432 -0.5995273590087891 -0.14020633697509766 -0.14020633697509766
7.402000427246094 -0.5791966915130615 -1.191494107246399 -0.0861053466796875 -0.16510009765625 -0.16510009765625
7.390000343322754 -0.5936606526374817 -1.2063286304473877 -0.4810619354248047 -0.6194562911987305 -0.6194524765014648
7.40000057220459 -0.56300288438797 -1.1234920024871826 

7.4205002784729 -0.6122783422470093 -1.2126638889312744 -0.3017991781234741 -0.66672682762146 -0.66672682762146
7.392500400543213 -0.5566818714141846 -1.1409791707992554 -1.6097955703735352 -0.9526252746582031 -0.9526233673095703
7.431500434875488 -0.5898599028587341 -1.2130733728408813 -0.044483184814453125 -1.5886101722717285 -1.5886139869689941
7.399500370025635 -0.6041349172592163 -1.224528193473816 -0.7083568572998047 -0.3299407958984375 -0.3299446105957031
7.390500545501709 -0.6014017462730408 -1.215614914894104 -1.027933120727539 -0.3575611114501953 -0.3575611114501953
7.434000492095947 -0.5876955986022949 -1.186574935913086 -0.5791778564453125 -0.5655994415283203 -0.5656032562255859
7.408000469207764 -0.5791124105453491 -1.1699767112731934 -0.6377487182617188 -1.0338897705078125 -1.0338859558105469
7.382500171661377 -0.5967636704444885 -1.1888368129730225 -0.0187225341796875 -2.473356246948242 -2.473369598388672
7.431500434875488 -0.5972005724906921 -1.2049944400787354 -1.37704

7.447000503540039 -0.5809648633003235 -1.1792397499084473 -0.16236305236816406 -0.21213722229003906 -0.21213340759277344
7.410500526428223 -0.5799136161804199 -1.1874523162841797 -0.010221481323242188 -0.39080047607421875 -0.39080047607421875
7.450000286102295 -0.5810457468032837 -1.1500332355499268 -0.2464752197265625 -2.0454044342041016 -2.045405387878418
7.4085001945495605 -0.5767093300819397 -1.1535791158676147 -0.8937273025512695 -0.91815185546875 -0.9181556701660156
7.428000450134277 -0.5796142816543579 -1.1480293273925781 -0.1450796127319336 -2.3711318969726562 -2.3711318969726562
7.39900016784668 -0.5858197212219238 -1.1848406791687012 -0.3016796112060547 -0.3290824890136719 -0.32908058166503906
7.3585004806518555 -0.5912036895751953 -1.2066452503204346 -0.5524129867553711 -6.086662292480469 -6.086669921875
7.392500400543213 -0.5892523527145386 -1.170905351638794 -0.136474609375 -2.14370059967041 -2.1437063217163086
7.338500499725342 -0.5946574807167053 -1.1932519674301147 -0.0

7.3585004806518555 -0.5869296193122864 -1.1769976615905762 -0.2672462463378906 -0.41055870056152344 -0.4105567932128906
7.383500576019287 -0.5804921984672546 -1.1685409545898438 -0.6888980865478516 -2.5312023162841797 -2.531208038330078
7.428500175476074 -0.5773679614067078 -1.1825706958770752 -2.0747056007385254 -0.008754730224609375 -0.008754730224609375
7.4110002517700195 -0.5742334127426147 -1.1768616437911987 -0.18352127075195312 -1.5319557189941406 -1.5319557189941406
7.497500419616699 -0.5906134843826294 -1.2043603658676147 -0.42636680603027344 -0.009518623352050781 -0.009518623352050781
7.442500591278076 -0.5738289952278137 -1.1609249114990234 -1.4819560050964355 -3.314483642578125 -3.3144798278808594
7.440000534057617 -0.5797981023788452 -1.1807379722595215 -0.14530658721923828 -0.9392871856689453 -0.9392871856689453
7.466000556945801 -0.5656471252441406 -1.1238431930541992 -0.0042724609375 -0.2153463363647461 -0.2153472900390625
7.414000511169434 -0.5696981549263 -1.137913107

7.3575005531311035 -0.5933452248573303 -1.2112869024276733 -0.5545444488525391 -6.309202194213867 -6.30919075012207
7.375000476837158 -0.5820946097373962 -1.1895290613174438 -0.43128180503845215 -4.578044891357422 -4.578031539916992
7.368000507354736 -0.5793315768241882 -1.172522783279419 -1.5625686645507812 -1.351724624633789 -1.3517169952392578
7.4150004386901855 -0.5727061033248901 -1.1442451477050781 -1.3721466064453125 -1.6683158874511719 -1.6683101654052734
7.392000198364258 -0.5552619099617004 -1.1364033222198486 -1.0940475463867188 -0.6917504072189331 -0.6917465925216675
7.453000545501709 -0.5521286725997925 -1.1190634965896606 -0.6043415069580078 -1.1708259582519531 -1.1708259582519531
7.429500579833984 -0.5640996098518372 -1.1347424983978271 -0.6237449645996094 -0.1373988389968872 -0.1373988389968872
7.458500385284424 -0.5720592737197876 -1.1553840637207031 -0.0107879638671875 -0.03293418884277344 -0.03293418884277344
7.457500457763672 -0.5654320120811462 -1.1243518590927124 

In [17]:
evaluate(epochs = 10, npoints = 23, batchsize = 100)

24.15999984741211 -0.35418593883514404 -0.6184512376785278 -0.6444015502929688 -0.0172576904296875 -0.0172576904296875
24.549999237060547 -0.370974063873291 -0.7424271702766418 -0.069122314453125 -0.7429962158203125 -0.7430038452148438
24.149999618530273 -0.3767475485801697 -0.8144843578338623 -0.5967254638671875 -1.1064109802246094 -1.1064033508300781
24.869998931884766 -0.3185718357563019 -0.6442034840583801 -0.5806818008422852 -0.00211334228515625 -0.00211334228515625
24.469999313354492 -0.33120349049568176 -0.6414774656295776 -0.00731658935546875 -0.5432815551757812 -0.54327392578125
24.479999542236328 -0.2983148992061615 -0.7824031710624695 -1.142526626586914 -0.04439735412597656 -0.04439735412597656
24.479999542236328 -0.36322128772735596 -0.7240633964538574 -0.5587539672851562 -0.3613424301147461 -0.3613581657409668
24.649999618530273 -0.36174705624580383 -0.8161125183105469 -0.25240325927734375 -0.30452728271484375 -0.30455780029296875
24.739999771118164 -0.305260568857193 -0.6

In [3]:
def evaluate(epochs = 30000, npoints = 13, batchsize = 100, nsamples = 2):
    NN.eval()
    with torch.no_grad():
        for i in range(epochs):
            env.reset(npoints, batchsize, nsamples)
            """include the boundary points, kinda makes sense that they should contribute (atm only in the encoder, difficult to see how in the decoder)"""
            memory = NN.encode(env.points) #[npoints, batchsize * nsamples, emsize]
            #### #### #### remember to include tgt.detach() when reinstate with torch.no_grad()
            tgt = NN.start_token.unsqueeze(0).unsqueeze(1).expand(1, batchsize * nsamples, -1).detach() #[1, batchsize * nsamples, emsize]
            #with torch.no_grad(): #to speed up computation, selecting routes is done without gradient
            for j in range(3, npoints):
                #### #### #### remember to include memory.detach() when reinstate with torch.no_grad()
                _, logits = NN.decode_next(memory.detach(), tgt, env.points_mask)
                next_point = env.sampleandgreedy_point(logits)
                """
                for inputing the previous embedding into decoder
                """
                tgt = torch.cat([tgt, memory.gather(0, next_point.unsqueeze(0).unsqueeze(2).expand(1, -1, memory.size(2)))]) #[nsofar, batchsize * nsamples, emsize]
                """
                for inputing the previous decoder output into the decoder (allows for an evolving strategy, but doesn't allow for fast training
                """
                ############


            NN.eval()
            _, logprob = NN.calculate_logprob(memory, env.points_sequence) #[batchsize * nsamples]
            NN.train()
            """
            clip logprob so doesn't reinforce things it already knows
            TBH WANT SOMETHING DIFFERENT ... want to massively increase training if find something unexpected and otherwise not
            """
            
            greedy_baseline = env.cost.view(batchsize, nsamples)[:, -1] #[batchsize], greedy sample
            
            print(greedy_baseline.mean().item(), logprob.view(batchsize, nsamples)[:, -1].mean().item(), logprob.view(batchsize, nsamples)[:, :-1].mean().item(), logprob[batchsize - 1].item(), logprob[0].item(), env.logprob[0].item())
  

In [6]:
for i in range(10):
    random_insertion(53, 1000)

112.23300170898438 7.801767826080322
112.27400207519531 8.104974746704102
112.65799713134766 7.472407341003418
112.23100280761719 7.915952205657959
112.4520034790039 7.713442325592041
111.92400360107422 8.143373489379883
112.55699920654297 8.011175155639648
112.1729965209961 8.002193450927734
112.03600311279297 7.991656303405762
111.97899627685547 7.911330223083496
